<h1 style='color:blue'> Watershed challenge </h1>

<h2> Load libraries </h2>

In [406]:
import pandas as pd
import numpy as np 
from zipfile import ZipFile
from urllib.request import urlopen
import io
from sklearn import preprocessing
import datetime as dt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, plot_roc_curve
import scikitplot as skplt

from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier


In [63]:
pd.options.mode.chained_assignment = None


<h1 style='color:blue'> Challenge steps </h1>

<h2> 1) Load data </h2>

In [64]:
url = urlopen("https://github.com/SpikeLab-CL/challenge_watershed/raw/main/flux.csv.zip").read()
file = ZipFile(io.BytesIO(url))

df = pd.read_csv(file.open("flux.csv"))
df.head(10)

date  basin_id   flux  precip   temp_max                 gauge_name  \
0  1980-01-01   1001001  0.579     0.0  10.685653  Rio Caquena En Nacimiento   
1  1980-01-02   1001001  0.543     0.0  11.470960  Rio Caquena En Nacimiento   
2  1980-01-03   1001001  0.482     0.0  11.947457  Rio Caquena En Nacimiento   
3  1980-01-04   1001001  0.459     0.0  12.424489  Rio Caquena En Nacimiento   
4  1980-01-05   1001001  0.436     0.0  12.649203  Rio Caquena En Nacimiento   
5  1980-01-06   1001001  0.385     0.0  12.798975  Rio Caquena En Nacimiento   
6  1980-01-07   1001001  0.380     0.0  12.798241  Rio Caquena En Nacimiento   
7  1980-01-08   1001001  0.380     0.0  12.927674  Rio Caquena En Nacimiento   
8  1980-01-09   1001001  0.380     0.0  12.612116  Rio Caquena En Nacimiento   
9  1980-01-10   1001001  0.380     0.0  12.613236  Rio Caquena En Nacimiento   

       lat      lon    mean_elev   area_km2  
0 -18.0769 -69.1961  4842.449328  49.711859  
1 -18.0769 -69.1961  4842.449328  49.711859  
2 -18.0769 -69.1961  4842.449328  49.711859  
3 -18.0769 -69.1961  4842.449328  49.711859  
4 -18.0769 -69.1961  4842.449328  49.711859  
5 -18.0769 -69.1961  4842.449328  49.711859  
6 -18.0769 -69.1961  4842.449328  49.711859  
7 -18.0769 -69.1961  4842.449328  49.711859  
8 -18.0769 -69.1961  4842.449328  49.711859  
9 -18.0769 -69.1961  4842.449328  49.711859

<h2> 2) Perform EDA </h2>

<h3> 2.1 Checking basic info & missing values </h3>

In [65]:
df.info() # checking for number of columns, Dtypes and data size

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4180480 entries, 0 to 4180479
Data columns (total 10 columns):
 #   Column      Dtype  
---  ------      -----  
 0   date        object 
 1   basin_id    int64  
 2   flux        float64
 3   precip      float64
 4   temp_max    float64
 5   gauge_name  object 
 6   lat         float64
 7   lon         float64
 8   mean_elev   float64
 9   area_km2    float64
dtypes: float64(7), int64(1), object(2)
memory usage: 318.9+ MB


In [66]:
df.describe()

basin_id          flux        precip      temp_max           lat  \
count  4.180480e+06  4.180480e+06  4.175037e+06  4.175037e+06  4.180480e+06   
mean   7.179757e+06  5.253340e+01  2.947445e+00  1.365728e+01 -3.569572e+01   
std    3.180965e+06  1.676027e+02  8.766749e+00  6.615037e+00  8.047659e+00   
min    1.001001e+06  0.000000e+00  0.000000e+00 -1.160359e+01 -5.494690e+01   
25%    4.558001e+06  8.680000e-01  0.000000e+00  9.162867e+00 -3.915000e+01   
50%    7.350003e+06  5.171000e+00  0.000000e+00  1.321396e+01 -3.588420e+01   
75%    9.416001e+06  2.990000e+01  6.422626e-01  1.805745e+01 -3.126560e+01   
max    1.293000e+07  1.580500e+04  2.132120e+02  4.081117e+01 -1.784280e+01   

                lon     mean_elev      area_km2  
count  4.180480e+06  4.180480e+06  4.180480e+06  
mean  -7.129595e+01  1.760129e+03  2.404876e+03  
std    1.254339e+00  1.382121e+03  4.322051e+03  
min   -7.366670e+01  1.181229e+02  1.789123e+01  
25%   -7.231670e+01  5.847012e+02  3.761001e+02  
50%   -7.137190e+01  1.195311e+03  8.205541e+02  
75%   -7.050670e+01  3.048161e+03  2.461610e+03  
max   -6.763920e+01  4.910152e+03  5.224367e+04

In [67]:
df.isnull().sum() # checking for missing values. In this case there are 2 columns with missing values

date             0
basin_id         0
flux             0
precip        5443
temp_max      5443
gauge_name       0
lat              0
lon              0
mean_elev        0
area_km2         0
dtype: int64

In [68]:
print("Max percent of missing values equals to", df.isnull().sum().max()/len(df) * 100,"%")

Max percent of missing values equals to 0.13020035976729946 %


In [69]:
pd.Series({col:df[col].nunique() for col in df}) # number of unique values per column

date            14768
basin_id          503
flux            35978
precip        1384281
temp_max      3901982
gauge_name        503
lat               485
lon               454
mean_elev         500
area_km2          500
dtype: int64

<h3> 2.2 Data cleansing  </h3>

In [70]:
# Removing records with NA to easier further analysis. This can be done without harming the final results because 
# the ammount of NA values is relatively insignificant (~ 0.1%)

df = df.dropna()

<h3> 2.3 Univariate analysis  </h3>

In [460]:
n_watersheds = df.groupby('date')['basin_id'].nunique().reset_index()

fig = px.line(n_watersheds, x='date', y="basin_id")
fig.update_layout(title_text="# watersheds per day")

fig.show()

In [452]:
df["year"] = pd.to_datetime(df["date"]).dt.year

df_ext = df.groupby(["year"])[["flux","temp_max","precip"]].mean().reset_index()

fig = make_subplots(rows=3, cols=1, subplot_titles =["Flux extreme","Temp extreme","Precip extreme"])

fig.append_trace(go.Scatter(
    x=df_ext["year"],
    y=df_ext["flux"],
    name = "Flux extreme"
), row=1, col=1)


fig.append_trace(go.Scatter(
    x=df_ext["year"],
    y=df_ext["temp_max"],
    name = "Temp extreme"
), row=2, col=1)


fig.append_trace(go.Scatter(
    x=df_ext["year"],
    y=df_ext["precip"],
    name = "Precip extreme"
), row=3, col=1)

fig.update_layout(title_text="Daily mean of cases across watersheds",
                 height=800) 


fig.show()

<h2> 3) Plot flux, temperature and precipitations</h2>

<h3> 3.1) Unique time-series plotting function for a station</h3>

In [75]:
def plot_one_timeserie(cod_station, variable, min_date = df["date"].min(), max_date = df["date"].max(), data = df ):
    ''' Plot a time series for a specific variable and station between two given periods.
    
    Args:
        cod_station: integer. Id for the station. 
        variable: string. Variable needed to plot. It can be one of the following values: ["flux","precip","temp_max"]
        min_date = string, optional. Needed format = "YYYY-MM-DD". Default = min() date of "flux.csv" date. 
        min_date = string, optional. Needed format = "YYYY-MM-DD". Default = max() date of "flux.csv" date. 
        data = pd.DataFrame, optional. Needed pd.Dataframe with the information of "flux.csv". 
            
    Returns:
        Plotly object with a graph of the time-series for the given arguments.
    
    '''    
    data_plot = data[data["basin_id"] == cod_station] 
    
    fig = px.line(data_plot, x='date', y=variable, range_x=[min_date, max_date]) 
    fig.update_layout(title_text=f'Time-series of {variable} between {min_date} and {max_date}') 

    fig.show()


In [76]:
# Function examples 

#Example 1 
plot_one_timeserie(12930001, "temp_max","2005-10-01","2020-01-01")

In [77]:
#Example 2
plot_one_timeserie(1001001, "flux","1980-01-01","2004-01-01")

<h3> 3.2) Multiple time-series plotting function for a station</h3>

In [78]:
def plot_three_timeseries(cod_station, min_date = df["date"].min(), max_date = df["date"].max(), data = df ):
    ''' Plot a time series for a specific variable and station between two given periods.
    
    Args:
        cod_station: integer. Id for the station. 
        variable: string. Variable needed to plot. It can be one of the following values: ["flux","precip","temp_max"]
        min_date = string. Needed format = "YYYY-MM-DD". Default = min() date of "flux.csv" date. 
        min_date = string. Needed format = "YYYY-MM-DD". Default = max() date of "flux.csv" date. 
        data = pd.DataFrame, optional. Needed pd.Dataframe with the information of "flux.csv". 
            
    Returns:
        Plotly object with a graph of 3 time-series for the given dates. Variables are normalized for easier comparison.
    
    '''    
    data_plot = data[data["basin_id"] == cod_station] 
    
    data_plot["flux"] = (data_plot["flux"]-data_plot["flux"].min())/(data_plot["flux"].max()-data_plot["flux"].min())
    data_plot["precip"] = (data_plot["precip"]-data_plot["precip"].min())/(data_plot["precip"].max()-data_plot["precip"].min())
    data_plot["temp_max"] = (data_plot["temp_max"]-data_plot["temp_max"].min())/(data_plot["temp_max"].max()-data_plot["temp_max"].min())
    
    fig = px.line(data_plot, x='date', y=data_plot[["flux","precip","temp_max"]].columns, range_x=[min_date, max_date]) 
    
    fig.update_layout(title_text=f'Time-series of variables flux, precip, temp_max  between {min_date} and {max_date}') 
    fig.update_traces(opacity=0.5)
    
    fig.show()



In [79]:
# Function examples 

#Example 1 
plot_three_timeseries(1001001,"2000-01-01","2004-01-01")

In [80]:
#Example 2
plot_three_timeseries(12930001,"2016-01-01","2020-01-01")

<h2> 4) Create specific variables</h2>

<h3> 4.1) Comments on variable definition </h3>

With the given example for an extreme value: 
<br>
*(...) a flux can be considered as extreme (value 1) when is over the 95 percentile of the flux distribution for that specific season (...)*.

One can take this example and create the variable using the following definitions: 

1) <u>Watershed level granularity</u>: Higher 5% of flux for every watersheds per season 
<br>
2) <u>Global level granularity</u>: Higher 5% of flux within all watersheds per season


In this study I decided to use the first definition, generating extreme values for every watersheds instead of using a global approach to finding extreme cases. I decided that because I noticed that there're watersheds with natural condition that'll generate biased results in favor to them, for example watersheds that are part of Baker River(gauge_name variable contains Rio Baker). An example of that case can be observed in the following plot.



In [81]:
# Add season column 
date_temp = pd.to_datetime(df["date"]).dt.month*100 + pd.to_datetime(df["date"]).dt.day # variable to help adding check seasons
df['season'] = (pd.cut(date_temp,[0,321,620,922,1220,1300],
                       labels=['Summer','Fall','Winter','Spring','Summer'],
                      ordered = False)
                  .str.strip()
               )

# Add extreme variables for given rule (1 if value over 95 percentile for a specific season, else 0 )
df["flux_extreme"] = df.groupby(["season"])["flux"].rank(pct=True)
df["temp_extreme"] = df.groupby(["season"])["temp_max"].rank(pct=True)
df["precip_extreme"] = df.groupby(["season"])["precip"].rank(pct=True)

df["flux_extreme"] = np.where(df["flux_extreme"] >.95,1,0)
df["temp_extreme"] =  np.where(df["temp_extreme"] >.95,1,0)
df["precip_extreme"] =  np.where(df["precip_extreme"] >.95,1,0)

df_flux = df.groupby(["basin_id","gauge_name"])["flux_extreme"].mean().reset_index()
df_flux = df_flux[df_flux["flux_extreme"] > 0]

fig = px.bar(df_flux, y='gauge_name', x='flux_extreme',orientation='h', color = 'flux_extreme')
fig.update_layout(title_text="Mean global flux extreme per watershed - Non zero values for watershed",
                 yaxis= {'categoryorder':'total ascending',"tickfont":dict(size=10) },
                 height=1600) 

fig.show()

<h3> 4.1) Generating season and extreme variables</h3>

In [214]:
# Add season column 
date_temp = pd.to_datetime(df["date"]).dt.month*100 + pd.to_datetime(df["date"]).dt.day # variable to help adding check seasons
df['season'] = (pd.cut(date_temp,[0,321,620,922,1220,1300],
                       labels=['Summer','Fall','Winter','Spring','Summer'],
                      ordered = False)
                  .str.strip()
               )

# Add extreme variables for given rule (1 if value over 95 percentile for a specific season, else 0 )
df["flux_extreme"] = df.groupby(["season","basin_id"])["flux"].rank(pct=True)
df["temp_extreme"] = df.groupby(["season","basin_id"])["temp_max"].rank(pct=True)
df["precip_extreme"] = df.groupby(["season","basin_id"])["precip"].rank(pct=True)

df["flux_extreme"] = np.where(df["flux_extreme"] >.95,1,0)
df["temp_extreme"] =  np.where(df["temp_extreme"] >.95,1,0)
df["precip_extreme"] =  np.where(df["precip_extreme"] >.95,1,0)

df["year"] = pd.to_datetime(df["date"]).dt.year
df["month"] = pd.to_datetime(df["date"]).dt.month
df["week"] = pd.to_datetime(df["date"]).dt.isocalendar().week
df["decade"] = pd.to_datetime(df["date"]).dt.year // 10 * 10


<h3> 4.3) Comments on methodology </h3>

For an initial analysis I believe the given approach is useful, but there are ways to improve it. 


One of the weak point of this  approach  is that it doesn't consider the effects of natural trends over time (ex: increase in max temperature year over year) or cyclical effects. Because of that, multiple expected values could be considered extreme cases compared to results of previous years, overstimating the ammount of extreme values.

Another problem with this rule (over 95 percentile) is that is only consider the high values of a variable as an extreme value. That affects variables with low abnormal values the most, for example years with drought are not considered as extreme.


One solution to that is using a creating a time-series descomponation approach to identify trends and seasonal effects for every watershed independently, and then use a similar methodology to check the extreme upper and lower cases given a certain percentile (ex: quantile regression). A complement to this proposal is to first create clusters to help compare watershed and identify extreme values between watershed with similar conditions (ex: watersheds in a same region or location).

<h2> 5) Plot the variable flux_extreme</h2>

<h3> 5.1) Flux extreme over time</h3>

In [83]:
df_flux = df.groupby(["decade"])["flux_extreme"].mean().reset_index()
df_flux = df_flux[df_flux["flux_extreme"] < 1] #removing cases without variance per decade (flux_extreme == 1)

fig = px.bar(df_flux, y='flux_extreme', x='decade', color = 'flux_extreme')



fig.show()

As observed in the previous plot, in the last 2 decades the number of extreme flux cases has been decrease in aprox. 2BPS

<h3> 5.2) Flux extreme - Behaviour between watersheds</h3>

To check if there is a different behaviour among the watersheds, first I'll study the existence of variance across multiple decades. This'll help me understand the distribution of the flux extreme per watershed.

In [111]:
df_flux = df.groupby(["basin_id","gauge_name", "decade"])["flux_extreme"].mean().reset_index()
df_flux = df_flux[df_flux["flux_extreme"] < 1] #removing cases without variance per decade (flux_extreme == 1)

fig = px.scatter(df_flux, x="decade", y="flux_extreme", color="gauge_name")
fig.update_layout(title_text="Mean flux extreme per watershed") 

fig.show()

In [128]:
fig = px.box(df_flux, x="decade", y="flux_extreme", points="all")
fig.show()


The previous plots shows a lot of outliers for the 2000 and 2020 decades. 

Because there are watersheds with fewer years of information, I'll compare the watersheds that have 5 decades of data. This'll help identify de trends and differences among watersheds over the years for the cases with the most reliable information.

In [140]:
df_flux2 = df[df.groupby('basin_id')["decade"].transform('nunique') == 5]

df_flux2 = df_flux2.groupby(["basin_id","gauge_name", "decade"])["flux_extreme"].mean().reset_index()
df_flux2 = df_flux2[df_flux2["flux_extreme"] < 1] #removing cases without variance per decade (flux_extreme == 1)
df_flux2 = df_flux2[df_flux2.groupby('basin_id')["decade"].transform('nunique') == 5]


fig = px.box(df_flux2, x="decade", y="flux_extreme", points="all")
fig.show()

In [141]:
fig = px.scatter(df_flux2, x="decade", y="flux_extreme", color="gauge_name", trendline = "ols")

fig.update_layout(title_text="Mean flux extreme per watershed per decade") 

fig.show()


After excluding the watersheds with less than 5 decades of information, the total number of outliers decrease, being only the decade of 2020 the one that shows lots of outliers/very high values.

The graph below shows 3 different types of watersheds behaviour.


In [101]:
df_flux3 = df_flux2[df_flux2["gauge_name"].isin(["Rio Paine En Parque Nacional 2","Rio Las Minas En Bt. Sendos",'Rio Hurtado En San Agustin'])]

#fig = px.bar(df_flux, y='gauge_name', x='flux_extreme', z= "season", orientation='h', color = 'flux_extreme')
fig = px.scatter(df_flux3, x="decade", y="flux_extreme", color="gauge_name", trendline = "ols")


fig.update_layout(title_text="Mean flux extreme per watershed per decade - Selected cases with different trends") 

fig.show()

# Rio San Juan En Desembocadura 
# Rio Hurtado En San Agustin


<h3> 5.1 Plot discussion </h3>
<p> From the previous plot we can see differences between the watersheds behaviours, existing three main trends (increase, decrease and stay the same over time), but the cases with watersheds that increase over the last decade are very few. Further analysis are needed to conclude if those cases are outliers or not, but for the given sample we can conclude the existence of different behaviours among watersheds. 
   
    
Further studies  include change the timeframe of analysis (ex: every 5 years), creating cluster over watershed locations and perform analysis with more relaxed conditions (not only watersheds with 5 decades of information).    
    
</p>
    
    
    

<h2> 6) Extreme cases over time</h2>

<h3> 6.1) Daily plot</h3>

In [143]:
df_ext = df.groupby(["date"])[["flux_extreme","temp_extreme","precip_extreme"]].mean().reset_index()
fig = make_subplots(rows=3, cols=1, subplot_titles =["Flux extreme","Temp extreme","Precip extreme"])

fig.append_trace(go.Scatter(
    x=df_ext["date"],
    y=df_ext["flux_extreme"],
    name = "Flux extreme"
), row=1, col=1)


fig.append_trace(go.Scatter(
    x=df_ext["date"],
    y=df_ext["temp_extreme"],
    name = "Temp extreme"
), row=2, col=1)


fig.append_trace(go.Scatter(
    x=df_ext["date"],
    y=df_ext["precip_extreme"],
    name = "Precip extreme"
), row=3, col=1)

fig.update_layout(title_text="Daily mean of extreme cases across watersheds",
                 height=800) 


fig.show()

Looking at the daily data, it's difficult to see if there is any frequency change over time.

<h3> 6.1) Yearly plot</h3>

In [146]:
df_ext = df.groupby(["year"])[["flux_extreme","temp_extreme","precip_extreme"]].mean().reset_index()

fig = make_subplots(rows=3, cols=1, subplot_titles =["Flux extreme","Temp extreme","Precip extreme"])

fig.append_trace(go.Scatter(
    x=df_ext["year"],
    y=df_ext["flux_extreme"],
    name = "Flux extreme"
), row=1, col=1)


fig.append_trace(go.Scatter(
    x=df_ext["year"],
    y=df_ext["temp_extreme"],
    name = "Temp extreme"
), row=2, col=1)


fig.append_trace(go.Scatter(
    x=df_ext["year"],
    y=df_ext["precip_extreme"],
    name = "Precip extreme"
), row=3, col=1)

fig.update_layout(title_text="Yearly mean of extreme cases across watersheds",
                 height=800) 


fig.show()

<h3> 6.2) Discussions </h3>

We can see a decrease in the percentage of flux extreme in comparison to its historical mean (0.05) from 2010. 

2020 looks like an abnormal year for precip extreme and temp extreme. Even if when we can see a different situation for 2020, the effect of that year alone isn't enough to conclude a sustained change in the frequency over time, but it could be a sign of a change in the historical trends.


<h2> 7) Extreme flux prediction </h2>


<h3> 7.1) Model proposal</h3>


<b>The proposal consists in different classifications models for predicting if a specific date will be an extreme flux value.</b>

<u>Main objetive</u>
<br>
Predict extreme flux probability for an specific day given past days weather and date information.
<br>

<u>Possible use cases for every watershed:</u>
<br>
1. Today's probability of being and extreme case given past data.
2. Simulate the probability that a given day will be an extreme case given certain conditions.

<u>Considerations & constraints </u>
<br>
1. The model will predict a day t using information of t-1 day and below. The model doesn't know the information or the future, but depending of the given information it could be used to predict the next day probability.

2. All the variables that are constanst per watershed (lat, lon, mean_elev, area_km2) will not be considered in this model, because the extreme flux values are constucted per watershed; therefore, the possible effect of the location or size of a watershed over the global average is not being reflected. 

3. The first value per watershed will not be considered because it's out of the scope of the model given the timeframe defined. 

<u>Model selection</u>
<br>
This model will be done using a Random Forest algorithm. This model was selected because it can be used for classification problems, it can handle missing values without any problems (even though they aren't any in this sample), and generally it has robust results. 





<h3> 7.2) Feature engineering</h3>


In [306]:
# yesterday values
df['flux1'] = df.groupby('basin_id')['flux'].shift()
df['temp_max1'] = df.groupby('basin_id')['temp_max'].shift()
df['precip1'] = df.groupby('basin_id')['precip'].shift()

df['flux_ext1'] = df.groupby('basin_id')['flux_extreme'].shift()
df['temp_ext1'] = df.groupby('basin_id')['temp_extreme'].shift()
df['precip_ext1'] = df.groupby('basin_id')['precip_extreme'].shift()


df['year1'] = df.groupby('basin_id')['year'].shift()
df['week1'] = df.groupby('basin_id')['week'].shift()
df['month1'] = df.groupby('basin_id')['month'].shift()
df['decade1'] = df.groupby('basin_id')['decade'].shift()

# moving average of past data 
df['flux_ma7'] = df.groupby('basin_id')['flux1'].transform(lambda x: x.rolling(7, 1).mean())
df['flux_ma30'] = df.groupby('basin_id')['flux1'].transform(lambda x: x.rolling(30, 1).mean())
df['flux_ma60'] = df.groupby('basin_id')['flux1'].transform(lambda x: x.rolling(60, 1).mean())
df['flux_ma90'] = df.groupby('basin_id')['flux1'].transform(lambda x: x.rolling(90, 1).mean())

df['flux_ext_ma7'] = df.groupby('basin_id')['flux_ext1'].transform(lambda x: x.rolling(7, 1).mean())
df['flux_ext_ma30'] = df.groupby('basin_id')['flux_ext1'].transform(lambda x: x.rolling(30, 1).mean())
df['flux_ext_ma60'] = df.groupby('basin_id')['flux_ext1'].transform(lambda x: x.rolling(60, 1).mean())
df['flux_ext_ma90'] = df.groupby('basin_id')['flux_ext1'].transform(lambda x: x.rolling(90, 1).mean())




In [307]:
df_model = df.drop(columns=["lat","lon","mean_elev","area_km2","gauge_name"]) # droping unused variables
df_model = df_model.drop(columns=["flux","precip", "temp_max",  "temp_extreme" , "precip_extreme","year","season","month","decade","week"]) # variables out of the timeframe (future values)
df_model = df_model.dropna() # deleting cases with NA (first value per watershed)

df_model.rename(columns={"flux_extreme":"target"}, inplace=True)



In [308]:
# grouped split for time series. Test data:last 60 days
train = []
test = []
for id in df_model["basin_id"].unique():
    
    temp = df_model[df_model["basin_id"]==id]
    
    train.append(temp.iloc[:-60,:]) 
    test.append(temp.iloc[-60:,:]) 
    
train = pd.concat(train, axis=0)
test = pd.concat(test, axis=0)



In [309]:
y_train = train["target"]
x_train = train.copy()
x_train.drop(columns=["target","date"], inplace=True)

y_test = test["target"]
x_test = test.copy()
x_test.drop(columns=["target","date"], inplace=True)

In [391]:
modelRF = RandomForestClassifier(n_estimators=20, min_samples_leaf = 1000, max_depth = 4) # this takes some minutes, feel free to reduce the n_estimator. 
#modelGB = GradientBoostingClassifier() # takes to long. Maybe for the next time :)  


In [392]:
modelRF.fit(x_train, y_train)
#modelGB.fit(x_train, y_train)


RandomForestClassifier(max_depth=4, min_samples_leaf=1000, n_estimators=20)

In [393]:
pred_gb = modelRF.predict(x_test)


<h2> 8) Model result analysis</h2>


<h3>8.1) Performance metrics</h3>

The following table shows the prediction result for the testing data. 

In [394]:
print(classification_report(y_test,pred_gb)) 

              precision    recall  f1-score   support

           0       0.98      1.00      0.99     28763
           1       0.90      0.57      0.70      1417

    accuracy                           0.98     30180
   macro avg       0.94      0.78      0.84     30180
weighted avg       0.98      0.98      0.97     30180



From this results we can observe:

1. The accuracy of the model is 0.98, it looks high but this is tricky because the sample almost all cases are 0 (5% of data is equal to 1), meaning that 
2. For this problem the main metrics should be the precision, recall or f-1 score(armonic mean of recall and precision). This is because we are more conserned on the positive values of the target (extreme cases) vs the overall performance of the predictions.



<h3>8.2) Feature importance</h3>

In [395]:
fig = px.bar(x=x_train.columns, y=modelRF.feature_importances_)
fig.update_layout(title_text="Feature importance",
                 xaxis= {'categoryorder':'total descending'}) 

fig.show()

The plot shows that the most important variables are the ones relative to previous extreme flux dates. This was expected because the flux doesn't disappear from one day to another. With that in mind, I was hoping to variables related to the precipitation or tempeture with a higher importance.

This results aren,'t the best but they can be used to identify the probability that a given date will be an extreme value. 



<h3>8.2) Changing treshold</h3>

To identify the treshold for the 70% extreme cases, I'll gain get the max probability that gets a gain of 70%.

In [450]:
gain = pd.DataFrame()

prob1 = pd.DataFrame(modelRF.predict_proba(x_test)[:,1], columns=["prob"])
gain = pd.concat([gain,prob1]) 
gain["result"] = y_test.values

gain = gain.sort_values(by=['prob'], ascending=False)
gain["perc"] = gain["result"].cumsum()/gain["result"].sum()

print("treshold to detect the 70% of extreme flux events", gain[gain["perc"] >=0.7]["prob"].max())
gain["new_tresh"] = np.where(gain["prob"] >= gain[gain["perc"] >=0.7]["prob"].max(),1,0)



treshold to detect the 70% of extreme flux events 0.35873445017678524


This model is not very useful because it overestimate the number of dates with extreme values. As seeing in the table below, all the prediction metrics are worse than the previos treshold. 

In [451]:
print(classification_report(y_test,gain["new_tresh"])) 


              precision    recall  f1-score   support

           0       0.95      0.96      0.96     28763
           1       0.08      0.07      0.07      1417

    accuracy                           0.92     30180
   macro avg       0.52      0.51      0.52     30180
weighted avg       0.91      0.92      0.92     30180

